<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#AB-Testing" data-toc-modified-id="AB-Testing-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>AB-Testing</a></span></li></ul></div>

# AB-Testing

![cats](images/cats.jpeg)


Imaginad que somos los cientificos de datos de la empresa de videojuegos Tactile Entertainment. Los desarrolladores del juego Cookie Cats pretenden introducir un cambio en el juego para aumentar la retencion de los jugadores. En cierto nivel del juego los jugadores se encuentran una puerta que les obliga a esperar o a pagar la app. Actualmente la puerta se encuentra en nivel 30 y se pretende pasar al nivel 40, para comprobar la retencion a 1 y 7 dias. Antes de realizar el cambio definitivo en el juego se raliza un test AB.

Los datos estan alojados en `data/cookie_cats.csv`. Nuestro grupo de control sera la version actual `gate_30` y el grupo de tratamiento sera la version `gate_40`. Debemos realizar el test para 1 dia de retencion `retention_1` y para 7 dias `retention_7`.

In [1]:
# librerias

import pandas as pd
import numpy as np
pd.options.plotting.backend = "plotly"

from statsmodels.stats.proportion import proportions_ztest, proportion_confint
from scipy.stats import norm, sem, beta

import plotly.express as px
import plotly.graph_objects as go
from bayes import *

In [2]:
# datos
c_cats = pd.read_csv('./data/cookie_cats.csv')
c_cats.head()

userid  version  sum_gamerounds  retention_1  retention_7
0     116  gate_30               3        False        False
1     337  gate_30              38         True        False
2     377  gate_40             165         True        False
3     483  gate_40               1        False        False
4     488  gate_40             179         True         True

In [3]:
c_cats.shape

(90189, 5)

In [4]:
# transformacion

# Testeo a 1 día

des_control = c_cats[c_cats.version == 'gate_30'].shape[0]
ret1_control = c_cats[(c_cats.version == 'gate_30') & (c_cats.retention_1==True)]['retention_1'].sum()
des_treat = c_cats[c_cats.version == 'gate_40'].shape[0]
ret1_treat = c_cats[(c_cats.version == 'gate_40') & (c_cats.retention_1==True)]['retention_1'].sum()

ret1_rate_cont = ret1_control/des_control
ret1_rate_treat = ret1_treat/des_treat

# Testeo a 7 días
ret7_control = c_cats[(c_cats.version == 'gate_30') & (c_cats.retention_7==True)]['retention_7'].sum()
ret7_treat = c_cats[(c_cats.version == 'gate_40') & (c_cats.retention_7==True)]['retention_7'].sum()

ret7_rate_cont = ret7_control/des_control
ret7_rate_treat = ret7_treat/des_treat

In [5]:
print(f'La tasa de retención de 1 día:\nControl: {ret1_rate_cont:.4f}\nTreat: {ret1_rate_treat:.4f}')

La tasa de retención de 1 día:
Control: 0.4482
Treat: 0.4423


In [6]:
print(f'La tasa de retención de 7 días:\nControl: {ret7_rate_cont:.4f}\nTreat: {ret7_rate_treat:.4f}')

La tasa de retención de 7 días:
Control: 0.1902
Treat: 0.1820


In [7]:
pd.crosstab(c_cats.version,c_cats.retention_1).plot(kind='bar',barmode='group')

In [8]:
print(f'La tasa de retención de 7 día:\nControl: {ret7_rate_cont:.4f}\nTreat: {ret7_rate_treat:.4f}')

La tasa de retención de 7 día:
Control: 0.1902
Treat: 0.1820


In [9]:
pd.crosstab(c_cats.version,c_cats.retention_7).plot(kind='bar',barmode='group')

In [10]:
# muestreo
alpha_C1, beta_C1 = ret1_control+1, des_control-ret1_control+1
alpha_T1, beta_T1 = ret1_treat+1, des_treat-ret1_treat+1

alpha_C7, beta_C7 = ret7_control+1, des_control-ret7_control+1
alpha_T7, beta_T7 = ret7_treat+1, des_treat-ret7_treat+1

In [11]:
# testeo para retention_1

beta1_control = beta(alpha_C1, beta_C1)
beta1_test = beta(alpha_T1, beta_T1)

In [78]:
def plot(betas, nombres,title):
    centro =betas[0].mean() - (betas[0].mean() - betas[1].mean())/2 
    x = np.linspace(centro - 0.012,centro+0.012,10000)
    fig = go.Figure()

    for bet, nom in zip(betas, nombres):
        y = bet.pdf(x)
        y_media = bet.mean()
        y_std = bet.std()

        fig.add_trace(go.Scatter(x=x, y=y, name=f'{nom}: Tasa de retención {y_media*100:.2f}% +/- {y_std*100:.2f}%'))

    fig.update_layout(legend=dict(x=1, 
                                  y=1,
                                  xanchor='right',
                                  yanchor = 'bottom'),
                      title = dict(text = title,
                                   font= dict(size=20)
                                   
                                  )
                     )  # Ubicación de la leyenda en la esquina superior derecha

    fig.show()

In [79]:
plot([beta1_control,beta1_test],['Control','Test'], 'Retención a 1 día')


In [ ]:
salto1 = (beta1_control.mean() - beta1_test.mean())/beta1_control.mean()
salto1

In [52]:
prob1 = calc_prob(beta1_control,beta1_test)
prob1

0.9627939748515354

In [53]:
print(f'El cambio de configuración del juego supondrá una caida en la retención a 1 día del {salto1*100:.2f}% con una probalidad del {prob1*100:.2f}% ')

El cambio de configuración del juego supondrá una caida en la retención a 1 día del 1.32% con una probalidad del 96.28% 


In [80]:
# testeo para retention_7

beta7_control = beta(alpha_C7, beta_C7)
beta7_test = beta(alpha_T7, beta_T7)
plot([beta7_control,beta7_test],['Control','Test'],'Retención a 7 días')

In [81]:
salto7 = (beta7_control.mean() - beta7_test.mean())/beta7_control.mean()
prob7 = calc_prob(beta7_control,beta7_test)
print(f'El cambio de configuración del juego supondrá una caida en la retención a 1 día del {salto7*100:.2f}% con una probalidad del {prob7*100:.2f}% ')

El cambio de configuración del juego supondrá una caida en la retención a 1 día del 4.31% con una probalidad del 99.92% 


In [82]:
# conclusiones
# Explica detalladamente las conclusiones obtenidas de. tu testeo.

# Método frecuentista 